In [4]:
import requests
from bs4 import BeautifulSoup
import pandas as pd

import time
import random

### 1. 마지막 페이지 번호 추출

In [ ]:
# limit tag 추출
url_home = 'https://fireballs.imo.net/members/imo_view/browse_reports?country=US|United%20States&state=&start_date=1995-01-01%2000:00:00&end_date=2014-12-31%2023:59:59&event=&event_id=&event_year=&page=1'

headers = {'User-Agent':'Mozilla/5.0 (X11; Linux x86_64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/141.0.0.0 Safari/537.36'}

res = requests.get(url_home, headers = headers)
soup = BeautifulSoup(res.text, 'html.parser')

# 마지막 페이지를 나타내는 tag
limit = soup.select('div.mb li a' )[-2].get_text()

# string type의 limit를 int type으로 변환
limit_int = int(limit)
limit_int

### 2. 유성우 데이터 셋 크롤링

In [21]:

# metheo dataset list 준비
metheo_dataset = []

# 1부터 limit_int까지의 숫자를 1씩 증가
for idx in range(1,limit_int+1, 1):
    
    #f_string을 이용하여 page번호를 하나씩 증가
    url = f'https://fireballs.imo.net/members/imo_view/browse_reports?country=US|United%20States&state=&start_date=1995-01-01%2000:00:00&end_date=2014-12-31%2023:59:59&event=&event_id=&event_year=&page={idx}'

    headers = {'User-Agent':'Mozilla/5.0 (X11; Linux x86_64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/141.0.0.0 Safari/537.36'}


    res = requests.get(url, headers = headers)
    soup = BeautifulSoup(res.text, 'html.parser')

    # 각 페이지의 링크를 추출하는 tag
    links = [s.attrs['href'] for s in soup.select('tbody tr a')]
    for link in soup.select('tbody tr a'):
        link_temp = link.attrs['href']

        # report가 포함된 링크만 사용
        if 'report' in link_temp:
            # 뒤에 붙는 링크만 전달 추출되어 전체 링크를 만들기 위해 링크의 앞부분과 합침
            full_link = 'https://fireballs.imo.net/' + link_temp
            
            res = requests.get(full_link, headers = headers)
            soup = BeautifulSoup(res.text, 'html.parser')


            # key
            keys = soup.select('div.col-md-6 table tbody th')
            # value
            values = soup.select('div.col-md-6 table tbody td')
            
            # key
            remark_keys= soup.select('table.table th.col-xs-2')
            # value
            remark_values= soup.select('table.table td.col-xs-10')

            # dict type의 데이터를 위해 빈 dict 형식 변수 선언
            table = {}
            
            # key, value를 자동으로 추가
            for key, value in zip(keys, values):
                key_text = key.get_text()
                value_text = value.get_text()
                table[key_text] = value_text
                
            # remark_key, remark_value를 자동으로 추가
            for rk, rv in zip(remark_keys, remark_values):
                rk_text = rk.get_text()
                rv_text = rv.get_text()
                table[rk_text] = rv_text

            # metheo dataset list에 내용이 채워진 table을 append
            metheo_dataset.append(table)


            # 1~3 사이의 정수를 무작위로 입력하여 
            # time.sleep
            rand_time = random.randint(1, 3)
            time.sleep(rand_time)

            # 데이터 확인용 프린팅
            print(table)


{'Address': 'Leilani Estates, HI', 'Latitude': '19°', 'Longitude': ' -154°', 'Elevation': '231m', 'Local Date & Time': '1997-03-27 02:00 HST', 'UT Date & Time': '1997-03-27 12:00 UT', 'Duration': '-', 'Moving direction': 'From up left to down right', 'Descent Angle': '98°', 'Facing azimuth': '4.5°', 'First azimuth': '8.13°', 'First elevation': '31°', 'Last azimuth': '150.79°', 'Last elevation': '13°', 'Stellar Magnitude': '-16', 'Color': 'White', 'Observation': 'No', 'Remarks': 'I was sound asleep and saw 2 white eggs, it was the light comining through my eye sockets, bright enough to wake me up!! I opened my eyes to see a light 100 times brighter than sunlight! My body was gone, as was everything else in the room, only bright light!! I looked out towards the huge bdroom window to see it burn out over the tops of the trees, it reminded me of the flash of an old time camera flashbulb burning out!!Phenomenal! I hope I have the date right, almost 30 yrs ago!', 'Length': '-', 'Name': 'Debo

KeyboardInterrupt: 

### 3. DataFrame 만들기 & CSV 파일 저장

In [ ]:
df_metheo = pd.DataFrame(metheo_dataset)
df_metheo.to_csv('/Users/sungminhong/Documents/dev_ws/ufo_eda/data/metheo.csv')